In [1]:
import matplotlib
import matplotlib.pyplot as plt
import numpy as np
import pandas as pd
import sklearn

## 1. Get the Data

In [2]:
df = pd.read_csv(r'C:\\Users\\Jeeho\\Documents\\Python Scripts\\Capstone project\\Data\\full_data_set_v14(May4).csv', sep=';')

In [ ]:
df

In [3]:
pd.set_option('display.max_columns', None)

In [4]:
#See the full contents of the rows of value
pd.set_option('display.max_colwidth', -1)

In [5]:
pd.set_option('display.max_rows', None)

## 2. Prepare Data

### 2.1 Data Cleaning

In [6]:
# Replace '\N' values with null value
df = df.replace(r'\N', np.nan)

In [7]:
# Remove "$" sign
df= df.replace(r'\$','', regex=True) 

In [8]:
# Remove "%" Sign
df= df.replace(r'\%','', regex=True) 

In [9]:
# Remove "," Sign
df= df.replace(r'\,','', regex=True)

In [10]:
# Remove Object "#NULL!" 
df= df.replace('#NULL!','', regex=False)

In [11]:
# Remove \r in BoY, Country  Cluster, ivr
df= df.replace(r'\r','', regex=True) 

In [12]:
# Remove \r in BoY, Country  Cluster, ivr
df= df.replace(r'NaN','', regex=True) 

### 2.2 Feature selection

In [13]:
# drop rows with no values in 'country'
df = df[(df['ceo'].notnull())]

In [14]:
len(df)

1132

In [15]:
len(df['country'].notnull())

1132

In [16]:
display(df)

company_info_id   rank                                company  year  \
0     1                1.0    Walmart                                2019   
2     3                3.0    Royal Dutch Shell                      2019   
5     6                6.0    Saudi Aramco                           2019   
6     7                7.0    BP                                     2019   
7     8                8.0    Exxon Mobil                            2019   
8     9                9.0    Volkswagen                             2019   
9     10               10.0   Toyota Motor                           2019   
10    11               11.0   Apple                                  2019   
11    12               12.0   Berkshire Hathaway                     2019   
12    13               13.0   Amazon.com                             2019   
15    16               16.0   Glencore                               2019   
17    18               18.0   Daimler                                2019   
18    19               19.0   CVS Health                             2019   
19    20               20.0   Total                                  2019   
21    22               22.0   Trafigura Group                        2019   
22    23               23.0   Hon Hai Precision Industry             2019   
23    24               24.0   EXOR Group                             2019   
24    25               25.0   AT&T                                   2019   
26    27               27.0   AmerisourceBergen                      2019   
27    28               28.0   Chevron                                2019   
28    29               29.0   Ping An Insurance                      2019   
29    30               30.0   Ford Motor                             2019   
31    32               32.0   General Motors                         2019   
32    33               33.0   Mitsubishi                             2019   
33    34               34.0   Honda Motor                            2019   
34    35               35.0   Costco Wholesale                       2019   
36    37               37.0   Alphabet                               2019   
39    40               40.0   Walgreens Boots Alliance               2019   
40    41               41.0   JPMorgan Chase & Co.                   2019   
44    45               45.0   Allianz                                2019   
45    46               46.0   AXA                                    2019   
46    47               47.0   Kroger                                 2019   
47    48               48.0   General Electric                       2019   
51    52               52.0   Japan Post Holdings                    2019   
52    53               53.0   BMW Group                              2019   
53    54               54.0   Phillips 66                            2019   
55    56               56.0   China Mobile Communications            2019   
56    57               57.0   Valero Energy                          2019   
57    58               58.0   Bank of America Corp.                  2019   
59    60               60.0   Microsoft                              2019   
60    61               61.0   Huawei Investment & Holding            2019   
61    62               62.0   Home Depot                             2019   
63    64               64.0   Nippon Telegraph & Telephone           2019   
65    66               66.0   Nissan Motor                           2019   
66    67               67.0   China Development Bank                 2019   
67    68               68.0   Boeing                                 2019   
68    69               69.0   Wells Fargo                            2019   
69    70               70.0   Siemens                                2019   
70    71               71.0   Citigroup                              2019   
71    72               72.0   Marathon Petroleum                     2019   
74    75               75.0   Comcast                                2019   
75

In [ ]:
# drop rows with no values in 'country'
#df_ctry = df[(df['country'].notnull())] <-- Keep the rows for the volumn of the data and impose median value later

In [ ]:
# Drop rows with no values for Globe project values
# df_c = df_ctry[(df_ctry['country.1'].notnull())]    <--- Keep the rows for the volumns of the data and impose median value later

In [17]:
# Drop un necessary columns for ML process
df_ml = df.drop(['company_info_id', 'Years on Global 500 List', 'Website','Country Name', 'g_societal_culture_id', 'g_leadership_id',
           'Country Name.1', 'Country Cluster.1', 'hofstede_id', 'ctr', 'country.1','company', 'HQ Location', 'ceo', 'Born', 'education', 'rank',
            'employees', 'revenues_$m', 'profit_$m', 'assets_$m', 'profit_as_%_of_revenues', 'profits_as_%_of_assets', 'profits_as_%_of_stockholder_equity'], axis = 1)

In [18]:
# Drop rows if any of them have null cultural values
df_ml = df_ml[(df_ml['Country Cluster'].notnull())]  #<--- To encoding as one of categorical variaibles
# df_ml = df_ml[(df_ml['ivr'].notnull())]   <---- Keep the values

In [ ]:
#df_ml2 = df_ml

In [19]:
df_ml["total_stockholder_equity_$m"].isna(). sum()

0

In [20]:
# Change the data types of numeric values

cols = df_ml.columns.drop(['sector', 'industry', 'country', 'Country Cluster', 'year'])

df_ml[cols] = df_ml[cols].apply(pd.to_numeric, errors='coerce')

In [21]:
len(df_ml)

888

### 2.3 Split Dataset

In [29]:
#Split data set
from sklearn.model_selection import train_test_split
train_set, test_set = train_test_split(df_ml, test_size=0.1, random_state=42)

In [30]:
#Drop Label(Target Variable) for training set
df_ml_train = train_set.drop("total_stockholder_equity_$m", axis=1) # drop labels for training set
df_ml_labels = train_set["total_stockholder_equity_$m"].copy()

In [31]:
# Create numeric variables from the training sets
df_ml_num = df_ml_train.drop(['sector', 'industry', 'country', 'Country Cluster', 'year'], axis = 1)

In [32]:
# Cleaning numeric variables
try:
    from sklearn.impute import SimpleImputer # Scikit-Learn 0.20+
except ImportError:
    from sklearn.preprocessing import Imputer as SimpleImputer

In [33]:
imputer = SimpleImputer(strategy="median")  

In [34]:
imputer.fit(df_ml_num)

SimpleImputer(add_indicator=False, copy=True, fill_value=None,
              missing_values=nan, strategy='median', verbose=0)

In [35]:
X = imputer.transform(df_ml_num)

In [36]:
df_ml_tr = pd.DataFrame(X, columns=df_ml_num.columns)

In [37]:
#Get categorical values

df_ml_cat = df_ml_train[['sector', 'industry', 'country', 'Country Cluster','year']]

### 2.4 Feature Engineering
- Categorical variables

In [38]:
from sklearn.preprocessing import OrdinalEncoder

cat_encoder = OrdinalEncoder()
df_cat_1hot = cat_encoder.fit_transform(df_ml_cat)
df_cat_1hot

array([[16., 42.,  9.,  7.,  3.],
       [19., 53., 27.,  7.,  0.],
       [ 4., 59.,  9.,  7.,  1.],
       ...,
       [ 4., 14., 32.,  8.,  0.],
       [ 4., 45.,  9.,  7.,  1.],
       [ 9., 46., 34.,  2.,  3.]])

### 2.5 Feature Scaling (Included in 2.6)

-  Standardization

### 2.6 All in One Pipeline 
    i. Feature Scaling: Standardization (StandardScaler)
    ii. 1)numeric pipeline=> 3) Full pipeline


In [39]:
# Import the necessary modules for scaling
from sklearn.preprocessing import StandardScaler
from sklearn.pipeline import Pipeline

In [40]:
#Pipeline for numeric features

num_pipeline = Pipeline([
                        ('imputer', SimpleImputer(strategy="median")),
                        ('std_scaler', StandardScaler())
                        ])

df_ml_num_tr = num_pipeline.fit_transform(df_ml_num)

In [41]:
df_ml_num_tr

array([[ 0.43707366, -1.14327297, -0.11428853, ...,  1.36664168,
         0.43620528, -0.31449747],
       [ 0.43707366,  0.39215882,  0.31259049, ...,  1.36664168,
        -0.16505065, -0.54749096],
       [-0.41676951, -1.14327297, -0.11428853, ...,  1.36664168,
         0.43620528, -0.31449747],
       ...,
       [ 0.86399525, -0.06179493,  1.4153613 , ...,  1.31977702,
        -0.24521811, -0.2562491 ],
       [ 0.43707366, -1.14327297, -0.11428853, ...,  1.36664168,
         0.43620528, -0.31449747],
       [ 1.82456882,  0.67254202, -0.70124719, ..., -0.50794493,
        -1.04689268,  0.85046999]])

In [42]:
# create pipeline for categorical features
# Latest Version
from sklearn.compose import ColumnTransformer

num_attribs = list(df_ml_num)
cat_attribs = ['sector', 'industry', 'country', 'Country Cluster', 'year']

full_pipeline = ColumnTransformer([
        ("num", num_pipeline, num_attribs),
        ("cat", cat_encoder, cat_attribs),
    ])

df_ml_prepared = full_pipeline.fit_transform(df_ml_train)

In [43]:
df_ml_prepared

array([[ 0.43707366, -1.14327297, -0.11428853, ...,  9.        ,
         7.        ,  3.        ],
       [ 0.43707366,  0.39215882,  0.31259049, ..., 27.        ,
         7.        ,  0.        ],
       [-0.41676951, -1.14327297, -0.11428853, ...,  9.        ,
         7.        ,  1.        ],
       ...,
       [ 0.86399525, -0.06179493,  1.4153613 , ..., 32.        ,
         8.        ,  0.        ],
       [ 0.43707366, -1.14327297, -0.11428853, ...,  9.        ,
         7.        ,  1.        ],
       [ 1.82456882,  0.67254202, -0.70124719, ..., 34.        ,
         2.        ,  3.        ]])

## 3. Build and Evaluate Models

### 3.1 Train Many Models

#### 3.1.1. Linear Regression

In [44]:
from sklearn.linear_model import LinearRegression

lin_reg = LinearRegression()
lin_reg.fit(df_ml_prepared, df_ml_labels)

LinearRegression(copy_X=True, fit_intercept=True, n_jobs=None, normalize=False)

In [45]:
# let's try the full preprocessing pipeline on a few training instances
some_data = df_ml.iloc[:5]
some_labels = df_ml_labels.iloc[:5]
some_data_prepared = full_pipeline.transform(some_data)

print("Predictions:", lin_reg.predict(some_data_prepared))

Predictions: [46602.21670555 54074.68147969 57296.74140194 56622.73621686
 36273.59191451]


C:\Users\Jeeho\Anaconda3\lib\site-packages\sklearn\compose\_column_transformer.py:430: FutureWarning: Given feature/column names or counts do not match the ones for the data given during fit. This will fail from v0.24.
  FutureWarning)


In [47]:
#Compare against the actual values:

print("Labels:", list(some_labels))

Labels: [40629.1, 19433.0, 20159.0, 12974.3, 31934.0]


It works, although the predictions are not exactly accurate. Let’s measure this regression model’s RMSE on the whole training set using Scikit-Learn’s mean_squared_error function:

Used RMSE rather than MSE since there are too many outliers

In [48]:
from sklearn.metrics import mean_squared_error
df_ml_predictions = lin_reg.predict(df_ml_prepared)
lin_mse = mean_squared_error(df_ml_labels, df_ml_predictions)
lin_rmse = np.sqrt(lin_mse)
lin_rmse

51445.01619637518

In [76]:
lin_reg.score(df_ml_prepared, df_ml_labels)

0.05690890811546245

The RMSE is too high.

In [49]:
# Check the mean of label feature
t = train_set['total_stockholder_equity_$m'].astype(float)

In [50]:
t.mean()

40368.61664580727

#### 3.1.2. Decision Tree Regressor

In [52]:
# Try Decision Tree Regressor
from sklearn.tree import DecisionTreeRegressor

tree_reg = DecisionTreeRegressor()
tree_reg.fit(df_ml_prepared, df_ml_labels)

DecisionTreeRegressor(ccp_alpha=0.0, criterion='mse', max_depth=None,
                      max_features=None, max_leaf_nodes=None,
                      min_impurity_decrease=0.0, min_impurity_split=None,
                      min_samples_leaf=1, min_samples_split=2,
                      min_weight_fraction_leaf=0.0, presort='deprecated',
                      random_state=None, splitter='best')

In [53]:
df_ml_tree_predictions = tree_reg.predict(df_ml_prepared)
tree_mse = mean_squared_error(df_ml_labels, df_ml_tree_predictions)
tree_rmse = np.sqrt(tree_mse)
tree_rmse

12899.415444289974

In [75]:
tree_reg.score(df_ml_prepared, df_ml_labels)

0.9407065000795152

#### 3.1.3. Lasso Regression

In [54]:
from sklearn.linear_model import Lasso
import matplotlib.pyplot as plt
from matplotlib.pyplot import figure

In [55]:
lasso_reg = Lasso(alpha=0.1)
lasso_reg.fit(df_ml_prepared, df_ml_labels)

C:\Users\Jeeho\Anaconda3\lib\site-packages\sklearn\linear_model\_coordinate_descent.py:476: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 1007434861787.8843, tolerance: 224222790.53015286
  positive)


Lasso(alpha=0.1, copy_X=True, fit_intercept=True, max_iter=1000,
      normalize=False, positive=False, precompute=False, random_state=None,
      selection='cyclic', tol=0.0001, warm_start=False)

In [56]:
df_ml_lasso_predictions = lasso_reg.predict(df_ml_prepared)
lasso_mse = mean_squared_error(df_ml_labels, df_ml_lasso_predictions)
lasso_rmse = np.sqrt(lasso_mse)
lasso_rmse

51445.280533429795

In [77]:
lasso_reg.score(df_ml_prepared, df_ml_labels)

0.056899216425951527

Lasso regression's RMSE also too high

#### 3.1.4. Elastic-Net Regression

In [57]:
from sklearn.linear_model import ElasticNet

Elastic_reg = ElasticNet(alpha=1, l1_ratio=0.5)
Elastic_reg.fit(df_ml_prepared, df_ml_labels)

ElasticNet(alpha=1, copy_X=True, fit_intercept=True, l1_ratio=0.5,
           max_iter=1000, normalize=False, positive=False, precompute=False,
           random_state=None, selection='cyclic', tol=0.0001, warm_start=False)

In [58]:
df_ml_elastic_predictions = Elastic_reg.predict(df_ml_prepared)
elastic_mse = mean_squared_error(df_ml_labels, df_ml_elastic_predictions)
elastic_rmse = np.sqrt(elastic_mse)
elastic_rmse

51831.880425664305

In [78]:
Elastic_reg.score(df_ml_prepared, df_ml_labels)

0.04267157059970339

#### 3.1.5. Random Forest Regression

In [59]:
from sklearn.ensemble import RandomForestRegressor

forest_reg = RandomForestRegressor()
forest_reg.fit(df_ml_prepared, df_ml_labels)

RandomForestRegressor(bootstrap=True, ccp_alpha=0.0, criterion='mse',
                      max_depth=None, max_features='auto', max_leaf_nodes=None,
                      max_samples=None, min_impurity_decrease=0.0,
                      min_impurity_split=None, min_samples_leaf=1,
                      min_samples_split=2, min_weight_fraction_leaf=0.0,
                      n_estimators=100, n_jobs=None, oob_score=False,
                      random_state=None, verbose=0, warm_start=False)

In [60]:
df_ml_forest_predictions = forest_reg.predict(df_ml_prepared)
forest_mse = mean_squared_error(df_ml_labels, df_ml_forest_predictions)
forest_rmse = np.sqrt(lasso_mse)
forest_rmse

51445.280533429795

In [79]:
forest_reg.score(df_ml_prepared, df_ml_labels)

0.8398167475657464

__Decision Tree Regressor__ and __Random Forest Regressor__ show the highest and second hight accuracy scores as __0.94__ and __0.83__ respectively.  

__Decision Tree Regressor__  also shows the lowest RMSE as __12899.415__.

### 3.2 Measure and compare their performances using Cross-Validation

#### 3.2.1. Decision Tree Regression

In [61]:
def display_scores(scores):
    print("Scores:", scores)
    print("Mean:", scores.mean())
    print("Standard deviation:", scores.std())   

In [62]:
from sklearn.model_selection import cross_val_score

scores = cross_val_score(tree_reg, df_ml_prepared, df_ml_labels,
        scoring="neg_mean_squared_error", cv=10)

rmse_scores = np.sqrt(-scores)

display_scores(rmse_scores)

Scores: [69930.36049098 76282.58814736 58281.44102405 55512.97220364
 64310.09259062 66575.61064019 56556.89907524 66892.72370742
 61303.83440899 72129.88143205]
Mean: 64777.64037205484
Standard deviation: 6546.58131888217


In [63]:
tree_r_squared = cross_val_score(tree_reg, df_ml_prepared, df_ml_labels, scoring='r2', cv=10).mean()

tree_r_squared

-0.79985002455908

#### 3.2.2. Linear Regression

In [64]:
# Linear Regression
lin_scores = cross_val_score(lin_reg, df_ml_prepared, df_ml_labels,
            scoring="neg_mean_squared_error", cv=10)

lin_rmse_scores = np.sqrt(-lin_scores)
display_scores(lin_rmse_scores)


Scores: [46237.02719251 63267.38716211 55263.26830507 38620.82304241
 48857.92730619 36526.21614052 49135.18067915 56532.63811288
 60452.34508936 66592.236183  ]
Mean: 52148.50492131953
Standard deviation: 9550.050932294696


In [65]:
lin_r_squared = cross_val_score(lin_reg, df_ml_prepared, df_ml_labels, scoring='r2', cv=10).mean()

lin_r_squared

-0.03927624941321832

#### 3.2.3 Lasso Regression

In [66]:
# Lasso Regression

lasso_scores = cross_val_score(lasso_reg, df_ml_prepared, df_ml_labels,
            scoring="neg_mean_squared_error", cv=10)

lasso_rmse_scores = np.sqrt(-lasso_scores)
display_scores(lasso_rmse_scores)


C:\Users\Jeeho\Anaconda3\lib\site-packages\sklearn\linear_model\_coordinate_descent.py:476: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 928654591701.9357, tolerance: 205866731.72006574
  positive)
C:\Users\Jeeho\Anaconda3\lib\site-packages\sklearn\linear_model\_coordinate_descent.py:476: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 851112792082.0673, tolerance: 190393689.9782874
  positive)
C:\Users\Jeeho\Anaconda3\lib\site-packages\sklearn\linear_model\_coordinate_descent.py:476: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 792481449507.7389, tolerance: 199168434.0310796
  positive)
C:\Users\Jeeho\Anaconda3\lib\site-packages\sklearn\linear_model\_coordinate_descent.py:476: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality 

Scores: [46234.08517368 63287.15646929 55169.1117546  38617.90907664
 48759.1737941  36538.55134364 49138.07073267 56538.66714772
 60450.22501758 66599.20785317]
Mean: 52133.21583630994
Standard deviation: 9552.405443642985


C:\Users\Jeeho\Anaconda3\lib\site-packages\sklearn\linear_model\_coordinate_descent.py:476: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 918129109934.8926, tolerance: 205121159.40407136
  positive)
C:\Users\Jeeho\Anaconda3\lib\site-packages\sklearn\linear_model\_coordinate_descent.py:476: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 874840739052.4819, tolerance: 199039055.88840172
  positive)
C:\Users\Jeeho\Anaconda3\lib\site-packages\sklearn\linear_model\_coordinate_descent.py:476: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 874546524343.198, tolerance: 194179627.03513187
  positive)
C:\Users\Jeeho\Anaconda3\lib\site-packages\sklearn\linear_model\_coordinate_descent.py:476: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality

In [67]:
lasso_r_squared = cross_val_score(lasso_reg, df_ml_prepared, df_ml_labels, scoring='r2', cv=10).mean()

lasso_r_squared

C:\Users\Jeeho\Anaconda3\lib\site-packages\sklearn\linear_model\_coordinate_descent.py:476: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 928654591701.9357, tolerance: 205866731.72006574
  positive)
C:\Users\Jeeho\Anaconda3\lib\site-packages\sklearn\linear_model\_coordinate_descent.py:476: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 851112792082.0673, tolerance: 190393689.9782874
  positive)
C:\Users\Jeeho\Anaconda3\lib\site-packages\sklearn\linear_model\_coordinate_descent.py:476: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality gap: 792481449507.7389, tolerance: 199168434.0310796
  positive)
C:\Users\Jeeho\Anaconda3\lib\site-packages\sklearn\linear_model\_coordinate_descent.py:476: ConvergenceWarning: Objective did not converge. You might want to increase the number of iterations. Duality 

-0.03866487318620979

####  3.2.4. Elastic-Net Regression

In [68]:
elastic_scores = cross_val_score(Elastic_reg, df_ml_prepared, df_ml_labels,
            scoring="neg_mean_squared_error", cv=10)

elastic_rmse_scores = np.sqrt(-elastic_scores)
display_scores(elastic_rmse_scores)

Scores: [45904.86527883 63287.18460725 54888.25630989 38297.26325825
 47753.69436759 36053.53721255 48384.34013305 56442.00393982
 60543.23204486 65870.96754161]
Mean: 51742.53446936906
Standard deviation: 9646.300191788889


In [69]:
elastic_r_squared = cross_val_score(Elastic_reg, df_ml_prepared, df_ml_labels, scoring='r2', cv=10).mean()

elastic_r_squared

-0.02129888048164691

#### 3.2.5. Random Forest Regression

In [70]:
forest_scores = cross_val_score(forest_reg, df_ml_prepared, df_ml_labels,
            scoring="neg_mean_squared_error", cv=10)

forest_rmse_scores = np.sqrt(-forest_scores)
display_scores(forest_rmse_scores)

Scores: [47099.07074249 58694.22365455 51500.60097429 35475.47522268
 53581.27757477 38067.47562856 42079.2598633  49147.5758837
 50918.55836107 58490.47716462]
Mean: 48505.399507004346
Standard deviation: 7526.53720207373


In [71]:
forest_r_squared = cross_val_score(forest_reg, df_ml_prepared, df_ml_labels, scoring='r2', cv=10).mean()

forest_r_squared

0.08492877156224903

Only __Random Forest Regression__ model shows positive r_squared as __0.0849__.

### 3.3 Analyze the most significant variables for each algorithm

#### 3.3.1 Check standardized regression coefficients (which is after standardization of data)


### 3.4 The most promising model
 

## 4. Fine-tune the models

### 4.1. Fine-tune the hyperparameters using cross-validation
- GridSearch CV 

In [83]:
# GridSearch CV for Random Forest Regression
from sklearn.model_selection import GridSearchCV

param_grid = [
    # try 12 (3×4) combinations of hyperparameters
    {'n_estimators': [3, 10, 30], 'max_features': [2, 4, 6, 8]},
    # then try 6 (2×3) combinations with bootstrap set as False
    {'bootstrap': [False], 'n_estimators': [3, 10], 'max_features': [2, 3, 4]},
  ]

forest_reg = RandomForestRegressor(random_state=42)
# train across 5 folds, that's a total of (12+6)*5=90 rounds of training 
grid_search = GridSearchCV(forest_reg, param_grid, cv=5,
                           scoring='neg_mean_squared_error', return_train_score=True)
grid_search.fit(df_ml_prepared, df_ml_labels)

GridSearchCV(cv=5, error_score=nan,
             estimator=RandomForestRegressor(bootstrap=True, ccp_alpha=0.0,
                                             criterion='mse', max_depth=None,
                                             max_features='auto',
                                             max_leaf_nodes=None,
                                             max_samples=None,
                                             min_impurity_decrease=0.0,
                                             min_impurity_split=None,
                                             min_samples_leaf=1,
                                             min_samples_split=2,
                                             min_weight_fraction_leaf=0.0,
                                             n_estimators=100, n_jobs=None,
                                             oob_score=False, random_state=42,
                                             verbose=0, warm_start=False),
             iid='deprecated', n_jobs

In [84]:
grid_search.best_params_

{'max_features': 8, 'n_estimators': 30}

In [85]:
grid_search.best_estimator_

RandomForestRegressor(bootstrap=True, ccp_alpha=0.0, criterion='mse',
                      max_depth=None, max_features=8, max_leaf_nodes=None,
                      max_samples=None, min_impurity_decrease=0.0,
                      min_impurity_split=None, min_samples_leaf=1,
                      min_samples_split=2, min_weight_fraction_leaf=0.0,
                      n_estimators=30, n_jobs=None, oob_score=False,
                      random_state=42, verbose=0, warm_start=False)

In [ ]:
# find optimal alpha with grid search
#Elastic-Net regression
alpha = [0.001, 0.01, 0.1, 1, 10, 500, 1000, 1500]
l1_ratio = [0, 0.1, 0.2, 0.3, 0.4, 0.5, 0.6, 0.7, 0.8, 0.9, 1]
param_grid = dict(alpha=alpha, l1_ratio=l1_ratio)

grid_elastic = GridSearchCV(estimator=Elastic_reg, param_grid=param_grid, scoring='r2', verbose=1, n_jobs=-1)
grid_elastic_result = grid_elastic.fit(df_ml_prepared, df_ml_labels,)
print('Best Score: ', grid_elastic_result.best_score_)
print('Best Params: ', grid_elastic_result.best_params_)

In [ ]:
grid_elastic.best_estimator_
